<a href="https://colab.research.google.com/github/hazanyucel/DeepfakeDetection/blob/main/ROBERTa.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!git clone https://github.com/tizfa/tweepfake_deepfake_text_detection.git

Cloning into 'tweepfake_deepfake_text_detection'...
remote: Enumerating objects: 32, done.
remote: Counting objects: 100% (5/5), done.
remote: Compressing objects: 100% (5/5), done.
remote: Total 32 (delta 2), reused 0 (delta 0), pack-reused 27 (from 3)
Receiving objects: 100% (32/32), 2.82 MiB | 26.21 MiB/s, done.
Resolving deltas: 100% (7/7), done.


In [ ]:
import os

base_path = "tweepfake_deepfake_text_detection/data/splits"
print(os.listdir(base_path))


['validation.csv', 'train.csv', 'test.csv']


In [ ]:
import pandas as pd

df_train = pd.read_csv(f"{base_path}/train.csv", sep=';')
df_val = pd.read_csv(f"{base_path}/validation.csv", sep=';')
df_test = pd.read_csv(f"{base_path}/test.csv", sep=';')

df_train.head()


screen_name                                               text  \
0      imranyebot                             YEA now that note GOOD   
1          zawvrk  Listen to This Charming Man by The Smiths  htt...   
2        zawarbot  wish i can i would be seeing other hoes on the...   
3  ahadsheriffbot  The decade in the significantly easier schedul...   
4   kevinhookebot  "Theim class=\"alignnone size-full wp-image-60...   

  account.type class_type  
0          bot     others  
1        human      human  
2          bot     others  
3          bot     others  
4          bot        rnn

In [ ]:
# binary classification yapmak için etiketleri 1 ve 0 olarak düzenliyorum.
def map_label(class_type):
  return 0 if class_type== 'human' else 1

df_train['label']=df_train['class_type'].apply(map_label)
df_test['label']=df_test['class_type'].apply(map_label)
df_val['label']=df_val['class_type'].apply(map_label)


In [ ]:
import re

def cleanText(text):
  text = text.lower()
  text = re.sub(r"http\S+|www\S+", "", text)
  text = re.sub(r"@[A-Za-z0-9]+", "", text)
  text = re.sub(r"#\w+", "", text)
  text = re.sub(r"[^a-zA-Z\s]", "", text)
  text = re.sub(r"\s+", " ", text).strip()
  return text



In [ ]:
df_train['text_clean']=df_train['text'].astype(str).apply(cleanText)
df_test['text_clean']=df_test['text'].astype(str).apply(cleanText)
df_val['text_clean']=df_val['text'].astype(str).apply(cleanText)


In [ ]:
from transformers import RobertaTokenizer, RobertaForSequenceClassification

tokenizerRoberta = RobertaTokenizer.from_pretrained("roberta-base")
modelRoberta = RobertaForSequenceClassification.from_pretrained("roberta-base", num_labels=2)


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/481 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
import pandas as pd
import torch
from datasets import Dataset
from transformers import BertTokenizer, BertForSequenceClassification, Trainer
from transformers.training_args import TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

In [ ]:
df_train = pd.read_csv("/content/tweepfake_deepfake_text_detection/data/splits/train.csv", sep=";")
df_val   = pd.read_csv("/content/tweepfake_deepfake_text_detection/data/splits/validation.csv", sep=";")
df_test  = pd.read_csv("/content/tweepfake_deepfake_text_detection/data/splits/test.csv", sep=";")

# Etiket oluştur (0: human, 1: bot)
df_train['label'] = df_train['class_type'].apply(lambda x: 0 if x == 'human' else 1)
df_val['label'] = df_val['class_type'].apply(lambda x: 0 if x == 'human' else 1)
df_test['label'] = df_test['class_type'].apply(lambda x: 0 if x == 'human' else 1)

# Hepsini birleştir
df_all = pd.concat([df_train[['text', 'label']], df_val[['text', 'label']], df_test[['text', 'label']]])
df_all = df_all.dropna().sample(frac=1).reset_index(drop=True)  # shuffle


In [ ]:
dataset = Dataset.from_pandas(df_all)

In [ ]:
def tokenize_roberta(example):
    return tokenizerRoberta(example["text"], padding="max_length", truncation=True, max_length=128)

tokenized_dataset_roberta = dataset.map(tokenize_roberta, batched=True)


Map:   0%|          | 0/25572 [00:00<?, ? examples/s]

In [ ]:
tokenized_dataset_roberta.select(range(3))
# Tüm örnekleri yazdır
for i in range(len(tokenized_dataset_roberta)):
    print(tokenized_dataset_roberta[i])


Streaming output truncated to the last 5000 lines.
{'text': 'Old Feelings Come Back In New Ways.', 'label': 0, 'input_ids': [0, 26605, 22079, 1033, 8814, 3727, 96, 188, 24049, 4, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]}
{'text': "@shanselman I've noticed if you pass someone an Andr

In [23]:
from sklearn.model_selection import train_test_split
from datasets import Dataset

df_roberta=df_all[["text","label"]].dropna()
train_df,test_df=train_test_split(df_roberta,test_size=0.2,random_state=42)

train_dataset=Dataset.from_pandas(train_df.reset_index(drop=True))
test_dataset=Dataset.from_pandas(test_df.reset_index(drop=True))

train_tokenized=train_dataset.map(tokenize_roberta,batched=True)
test_tokenized=test_dataset.map(tokenize_roberta,batched=True)


Map:   0%|          | 0/20457 [00:00<?, ? examples/s]

Map:   0%|          | 0/5115 [00:00<?, ? examples/s]

In [35]:
from transformers import TrainingArguments, Trainer

training_args = TrainingArguments(
    output_dir="./roberta_results",
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    eval_strategy="epoch",
    save_strategy="epoch",
    logging_dir="./roberta_logs",
    logging_steps=10,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    report_to=None
)

Using the `WANDB_DISABLED` environment variable is deprecated and will be removed in v5. Use the --report_to flag to control the integrations used for logging result (for instance --report_to none).


In [36]:
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    preds = logits.argmax(axis=1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='binary')
    acc = accuracy_score(labels, preds)
    return {"accuracy": acc, "precision": precision, "recall": recall, "f1": f1}

In [37]:
trainer = Trainer(
    model=modelRoberta,
    args=training_args,
    train_dataset=train_tokenized,
    eval_dataset=test_tokenized,
    tokenizer=tokenizerRoberta,
    compute_metrics=compute_metrics
)

/tmp/ipython-input-37-1103380912.py:1: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [38]:
import os
os.environ["WANDB_DISABLED"] = "true"


In [39]:
trainer.train()

TrainOutput(global_step=3837, training_loss=0.23124073126763767, metrics={'train_runtime': 1515.1616, 'train_samples_per_second': 40.505, 'train_steps_per_second': 2.532, 'total_flos': 4036847144624640.0, 'train_loss': 0.23124073126763767, 'epoch': 3.0})

In [40]:
trainer.evaluate(eval_dataset=test_tokenized)


{'eval_loss': 0.37551671266555786,
 'eval_accuracy': 0.9085043988269794,
 'eval_precision': 0.9103829451243585,
 'eval_recall': 0.9053788771103258,
 'eval_f1': 0.9078740157480315,
 'eval_runtime': 35.5792,
 'eval_samples_per_second': 143.764,
 'eval_steps_per_second': 8.994,
 'epoch': 3.0}

In [41]:
trainer.save_model("./roberta_finetuned_model")


In [2]:
!pip install gradio transformers torch

import gradio as gr
from transformers import RobertaTokenizer, RobertaForSequenceClassification
import torch

# Model ve tokenizer yükleniyor
tokenizer = RobertaTokenizer.from_pretrained("./roberta_finetuned_model")
model = RobertaForSequenceClassification.from_pretrained("./roberta_finetuned_model")

def predict_tweet(text):
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding="max_length", max_length=128)
    with torch.no_grad():
        outputs = model(**inputs)
        probs = torch.softmax(outputs.logits, dim=1)
        pred = torch.argmax(probs).item()
        label = "🤖 Makine Üretimi" if pred == 1 else "🧠 İnsan"
        return f"{label} (Güven: {round(probs[0][pred].item(), 3)})"

gr.Interface(fn=predict_tweet, inputs="text", outputs="text", title="Tweet Deepfake Tespiti").launch()


It looks like you are running Gradio on a hosted a Jupyter notebook. For the Gradio app to work, sharing must be enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://87f871f88e4e1882f0.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
